Hello, my name is Aaron Kann, and this is an analysis on soccer stats.  The goal of this first analysis is to determine whether,
in general, a players last 5 stats are a better predictor of the next match's output as compared to the season to date.

In [2]:
import fbref_scrape as fbref

Firstly, the data for the premier league can be scraped through my code.  It will take a long time, so only uncomment the code if absolutely necessary.
The data should be stored in a folder called Premier_League_Matchlogs and accessed through there, so unless you are updating the folder, it is unnessecary to run the following code strip.

In [3]:
import json, csv, os
import pandas as pd
from constants import *
import numpy as np
from scipy.stats import poisson

# uncommenting the following line will scrape the premier league data
# fbref.SoccerLeague(fbref.premier_league_url, [7, 8])

C:\Users\Aaron\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\scipy\__init__.py:169: UserWarning: A NumPy version >=1.18.5 and <1.26.0 is required for this version of SciPy (detected version 1.26.4
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"


Next, we need to take the indiviual player's gamelogs and create a giant database of games.  
Because the variables we are trying to measure aren't explicitly within the data, we need to calculate them.

In [4]:
# read in the data
data_folder = 'Premier_League_Player_Matchlogs'
data_files = os.listdir(data_folder)
dfs = []

for file in data_files:
    if file.endswith('.csv'):
        file_path = os.path.join(data_folder, file)
        # read the csv file and process the data
        df = pd.read_csv(file_path)
        # df = add_name_to_df(df, file)
        dfs.append(df)

dfs[0].head()

game_started  game_count  games  minutes  gk_saves  clearances  tackles  \
0            Y           1      0       90         0           0        0   
1            Y           2      0       89         0           0        1   
2            Y           3      0       90         0           0        6   
3            Y           4      0       90         0           0        1   
4            Y           5      0       79         0           0        4   

   assisted_shots  fouled  shots  ...  sca  gca  passes_completed  passes_pct  \
0               0       0      2  ...    3    0                22        81.5   
1               0       0      1  ...    1    0                21        80.8   
2               0       0      1  ...    3    0                26        83.9   
3               0       0      4  ...    3    1                37        78.7   
4               0       0      0  ...    3    0                11        64.7   

   progressive_passes  carries  progressive_carries  take_ons take_ons_won  \
0                   3       20                    3         2            0   
1                   2       18                    2         2            2   
2                   4       30                    2         3            1   
3                   3       31                    3         1            1   
4                   1       16                    2         2            1   

   match_report  
0  Match Report  
1  Match Report  
2  Match Report  
3  Match Report  
4  Match Report  

[5 rows x 44 columns]

In [5]:
# def add_name_to_df(df, filename):
#     for row in df

def update_avgs(season_avgs, row, index):
    #iterate through the stats in season_avgs and update the averages
    for stat in season_avgs.keys():
        if stat in row.keys():
            season_avgs[stat] = (season_avgs[stat]*index + row[stat])/(index+1)
    return season_avgs

def update_last_five_avgs(last_five_avgs, df, index):
    #iterate through the stats in last_five_avgs and update the averages
    for stat in last_five_avgs.keys():
        if stat in df.keys():
            last_five_avgs[stat] = (last_five_avgs[stat]*5 + df.iloc[index][stat] - df.iloc[index-5][stat])/(5)
    return last_five_avgs

In [6]:
stats_wanted = fbref.get_stats_wanted('fbref')
stats_wanted.remove('name')
stats_wanted.remove('team')
stats_wanted.append('game_count')
df_as_list = list()

for i in range(len(dfs)): #iterates through each player's data
    
    # get rid of unwanted columns
    dfs[i] = dfs[i][stats_wanted]

    # create a new row, with the season totals as of matchweek 0 (ie all zero)
    season_avgs = pd.Series(data=[0]*len(stats_wanted), index=stats_wanted)
    last_five_avgs = pd.Series(data=[0]*len(stats_wanted), index=stats_wanted)
    # print(season_avgs, last_five_avgs)

    for index, row in dfs[i].iterrows(): #iterates through each game of each players data
        dfrow = pd.concat([row, season_avgs.add_suffix("_szn"), last_five_avgs.add_suffix("_l5")], axis=0)
        season_avgs = update_avgs(season_avgs, row, index)
        if index >= 5:
            last_five_avgs = update_last_five_avgs(last_five_avgs, dfs[i], index)
        else:
            last_five_avgs = update_avgs(last_five_avgs, row, index)

        df_as_list.append(dfrow)

    #end game loop
#end player loop
        


df = pd.DataFrame(df_as_list)
df.head()

l5 0 games              0
minutes            0
gk_saves           0
clearances         0
tackles            0
assisted_shots     0
fouled             0
shots              0
crosses            0
shots_on_target    0
passes             0
interceptions      0
fouls              0
goals              0
assists            0
cards_yellow       0
game_count         0
dtype: int64
games
stats
minutes
stats
gk_saves
stats
clearances
stats
tackles
stats
assisted_shots
stats
fouled
stats
shots
stats
crosses
stats
shots_on_target
stats
passes
stats
interceptions
stats
fouls
stats
goals
stats
assists
stats
cards_yellow
stats
game_count
stats
index 0
games
stats
minutes
stats
gk_saves
stats
clearances
stats
tackles
stats
assisted_shots
stats
fouled
stats
shots
stats
crosses
stats
shots_on_target
stats
passes
stats
interceptions
stats
fouls
stats
goals
stats
assists
stats
cards_yellow
stats
game_count
stats
l5 1 games               0
minutes            90
gk_saves            0
clearances          0
ta

C:\Users\Aaron\AppData\Local\Temp\ipykernel_19552\3444789560.py:13: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '89.5' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  season_avgs[stat] = (season_avgs[stat]*index + row[stat])/(index+1)


<class 'numpy.float64'>
(32, 17) 14
<class 'numpy.float64'>
(32, 17) 14
<class 'numpy.float64'>
(32, 17) 14
<class 'numpy.float64'>
(32, 17) 14
<class 'numpy.float64'>
(32, 17) 14
<class 'numpy.float64'>
(32, 17) 14
<class 'numpy.float64'>
(32, 17) 14
<class 'numpy.float64'>
(32, 17) 14
<class 'numpy.float64'>
(32, 17) 14
<class 'numpy.float64'>
(32, 17) 14
<class 'numpy.float64'>
(32, 17) 14
<class 'numpy.float64'>
(32, 17) 14
<class 'numpy.float64'>
(32, 17) 14
<class 'numpy.float64'>
(32, 17) 14
<class 'numpy.float64'>
(32, 17) 14
<class 'numpy.float64'>
(32, 17) 14
l5 15 games               0.0
minutes            89.8
gk_saves            0.0
clearances          0.0
tackles             1.4
assisted_shots      0.0
fouled              0.0
shots               1.4
crosses             0.0
shots_on_target     0.6
passes             27.0
interceptions       0.0
fouls               0.0
goals               0.4
assists             0.0
cards_yellow        0.6
game_count         13.0
dtype: flo

C:\Users\Aaron\AppData\Local\Temp\ipykernel_19552\3444789560.py:13: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '46.5' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  season_avgs[stat] = (season_avgs[stat]*index + row[stat])/(index+1)


games               0.0
minutes            58.8
gk_saves            0.0
clearances          0.0
tackles             0.6
assisted_shots      0.0
fouled              0.0
shots               0.0
crosses             0.0
shots_on_target     0.0
passes             30.2
interceptions       0.4
fouls               0.0
goals               0.0
assists             0.2
cards_yellow        0.0
game_count          4.0
dtype: float64
games
stats
minutes
stats
gk_saves
stats
clearances
stats
tackles
stats
assisted_shots
stats
fouled
stats
shots
stats
crosses
stats
shots_on_target
stats
passes
stats
interceptions
stats
fouls
stats
goals
stats
assists
stats
cards_yellow
stats
game_count
stats
index 6
<class 'numpy.float64'>
(28, 17) 6
<class 'numpy.float64'>
(28, 17) 6
<class 'numpy.float64'>
(28, 17) 6
<class 'numpy.float64'>
(28, 17) 6
<class 'numpy.float64'>
(28, 17) 6
<class 'numpy.float64'>
(28, 17) 6
<class 'numpy.float64'>
(28, 17) 6
<class 'numpy.float64'>
(28, 17) 6
<class 'numpy.float64'>
(28,

...

C:\Users\Aaron\AppData\Local\Temp\ipykernel_19552\3444789560.py:13: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '74.5' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  season_avgs[stat] = (season_avgs[stat]*index + row[stat])/(index+1)


games               0.0
minutes            85.8
gk_saves            0.0
clearances          0.0
tackles             1.0
assisted_shots      0.0
fouled              0.0
shots               2.6
crosses             0.0
shots_on_target     0.6
passes             15.6
interceptions       0.8
fouls               0.0
goals               0.2
assists             0.2
cards_yellow        0.2
game_count          7.0
dtype: float64
games
stats
minutes
stats
gk_saves
stats
clearances
stats
tackles
stats
assisted_shots
stats
fouled
stats
shots
stats
crosses
stats
shots_on_target
stats
passes
stats
interceptions
stats
fouls
stats
goals
stats
assists
stats
cards_yellow
stats
game_count
stats
index 9
<class 'numpy.float64'>
(34, 17) 9
<class 'numpy.float64'>
(34, 17) 9
<class 'numpy.float64'>
(34, 17) 9
<class 'numpy.float64'>
(34, 17) 9
<class 'numpy.float64'>
(34, 17) 9
<class 'numpy.float64'>
(34, 17) 9
<class 'numpy.float64'>
(34, 17) 9
<class 'numpy.float64'>
(34, 17) 9
<class 'numpy.float64'>
(34,

C:\Users\Aaron\AppData\Local\Temp\ipykernel_19552\3444789560.py:13: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '36.5' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  season_avgs[stat] = (season_avgs[stat]*index + row[stat])/(index+1)


games               0.0
minutes            68.2
gk_saves            0.0
clearances          0.0
tackles             1.8
assisted_shots      0.0
fouled              0.0
shots               0.6
crosses             0.0
shots_on_target     0.2
passes             41.4
interceptions       1.2
fouls               0.0
goals               0.0
assists             0.4
cards_yellow        0.0
game_count         13.0
dtype: float64
games
stats
minutes
stats
gk_saves
stats
clearances
stats
tackles
stats
assisted_shots
stats
fouled
stats
shots
stats
crosses
stats
shots_on_target
stats
passes
stats
interceptions
stats
fouls
stats
goals
stats
assists
stats
cards_yellow
stats
game_count
stats
index 15
<class 'numpy.float64'>
(32, 17) 15
<class 'numpy.float64'>
(32, 17) 15
<class 'numpy.float64'>
(32, 17) 15
<class 'numpy.float64'>
(32, 17) 15
<class 'numpy.float64'>
(32, 17) 15
<class 'numpy.float64'>
(32, 17) 15
<class 'numpy.float64'>
(32, 17) 15
<class 'numpy.float64'>
(32, 17) 15
<class 'numpy.float

games  minutes  gk_saves  clearances  tackles  assisted_shots  fouled  \
0    0.0     90.0       0.0         0.0      0.0             0.0     0.0   
1    0.0     89.0       0.0         0.0      1.0             0.0     0.0   
2    0.0     90.0       0.0         0.0      6.0             0.0     0.0   
3    0.0     90.0       0.0         0.0      1.0             0.0     0.0   
4    0.0     79.0       0.0         0.0      4.0             0.0     0.0   

   shots  crosses  shots_on_target  ...  shots_l5  crosses_l5  \
0    2.0      0.0              1.0  ...  0.000000         0.0   
1    1.0      0.0              0.0  ...  2.000000         0.0   
2    1.0      0.0              1.0  ...  1.500000         0.0   
3    4.0      0.0              3.0  ...  1.333333         0.0   
4    0.0      0.0              0.0  ...  2.000000         0.0   

   shots_on_target_l5  passes_l5  interceptions_l5  fouls_l5  goals_l5  \
0            0.000000       0.00          0.000000       0.0      0.00   
1            1.000000      27.00          0.000000       0.0      0.00   
2            0.500000      26.50          0.500000       0.0      0.00   
3            0.666667      28.00          0.666667       0.0      0.00   
4            1.250000      32.75          0.500000       0.0      0.25   

   assists_l5  cards_yellow_l5  game_count_l5  
0         0.0             0.00            0.0  
1         0.0             0.00            1.0  
2         0.0             0.00            1.5  
3         0.0             0.00            2.0  
4         0.0             0.25            2.5  

[5 rows x 51 columns]

In [7]:
df.shape

#save df as a csv file
df.to_csv('output.csv', index=False)


Now we have a list of every game played by a Premier League player, as well as their season and last 5 totals going into the game.

From here, we can use this data to determine what is a better predictor of a player's result by calculating the correlation of both variables

In [8]:
correlation_coefficient = df['passes'].corr(df['passes_l5'])
print(correlation_coefficient)

0.6359199085383154


In [9]:
correlation_coefficient = df['passes'].corr(df['passes_szn'])
print(correlation_coefficient)

0.6379006039559315


From here, we can see that, in determining the outcomes of the amount of passes a player would attempt, season averages were a slightly better indicator than last 5 averages.  